In [1]:
# Basic Imports
import os, shutil, time, copy
from pathlib import Path
import zipfile
import random
import numpy as np, pandas as pd
from tqdm.notebook import tqdm as tqdm_notebook # Use tqdm.notebook for Colab progress bars

import torch, torch.nn as nn, torch.optim as optim
from torch.utils.data import DataLoader, random_split
from torchvision import datasets, transforms, models
from sklearn.metrics import confusion_matrix, precision_score, recall_score, accuracy_score

In [2]:

# Colab Setup
from google.colab import drive
import os

# Mount Google Drive
print("Mounting Google Drive...")
drive.mount('/content/drive')
print("Google Drive mounted.")



# Set device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print("Device:", device)

Mounting Google Drive...
Mounted at /content/drive
Google Drive mounted.
Device: cuda


In [4]:

# PARAMETERS

# **1. Set the path to your ZIP file in Google Drive**
ZIP_PATH = "/content/drive/MyDrive/PR_Group_Project/defungi.zip"

# **2. Define the local folder where the images will be extracted**
LOCAL_DATA_DIR = "/content/drive/MyDrive/PR_Group_Project/unzipped"

print(f"Checking for ZIP file: {ZIP_PATH}")

if Path(ZIP_PATH).exists():
    print(" ZIP file found. Starting extraction...")

    # Create the target directory if it doesn't exist
    Path(LOCAL_DATA_DIR).mkdir(parents=True, exist_ok=True)

    # Unzip the file
    with zipfile.ZipFile(ZIP_PATH, 'r') as zip_ref:
        # We assume the subfolders (H1, H2, etc.) are at the root of the zip file,
        # so we extract directly into the local directory.
        zip_ref.extractall(LOCAL_DATA_DIR)

    # Set the DATA_ROOT to the local, unzipped folder
    DATA_ROOT = LOCAL_DATA_DIR
    print(f"Extraction complete. DATA_ROOT is set to: {DATA_ROOT}")
else:
    print(f" ERROR: ZIP file not found at {ZIP_PATH}. Please check the path.")
    DATA_ROOT = None # Prevent subsequent cells from running successfully



Checking for ZIP file: /content/drive/MyDrive/PR_Group_Project/defungi.zip
✅ ZIP file found. Starting extraction...
✅ Extraction complete. DATA_ROOT is set to: /content/drive/MyDrive/PR_Group_Project/unzipped


In [5]:
# Remaining Parameters
IMAGE_SIZE = 32
CLASS_NAMES = ['H1','H2','H3','H5','H6']
NUM_CLASSES = len(CLASS_NAMES)
RESULTS_DIR = "/content/drive/MyDrive/PR_Group_Project/results"
MODELS_DIR = f"{RESULTS_DIR}/models"
LOGS_DIR = f"{RESULTS_DIR}/logs"



# Create results folders
Path(RESULTS_DIR).mkdir(parents=True, exist_ok=True)
Path(MODELS_DIR).mkdir(parents=True, exist_ok=True)
Path(LOGS_DIR).mkdir(parents=True, exist_ok=True)
print(f"Results folders created under: {RESULTS_DIR}")

Results folders created under: /content/drive/MyDrive/PR_Group_Project/results


In [6]:
# Training params
BATCH_SIZE = 64
EPOCHS = 20
LR_LIST = [0.1, 0.01, 0.001]
MOMENTUM = 0.9
RANDOM_SEED = 42

# Pretrained comparison
PRETRAINED_EPOCHS = 3
PRETRAINED_LR = 0.001

MODEL1_PTH = None

In [7]:
# Data transforms
transform_basic = transforms.Compose([
    transforms.Resize((IMAGE_SIZE, IMAGE_SIZE)),
    transforms.ToTensor(),
    transforms.Normalize([0.485,0.456,0.406], [0.229,0.224,0.225])
])

# Load dataset from the local DATA_ROOT
print("Loading dataset from DATA_ROOT:", DATA_ROOT)
if DATA_ROOT is None:
    raise Exception("DATA_ROOT is not set. ZIP file extraction failed.")

balanced_dataset = datasets.ImageFolder(root=DATA_ROOT, transform=transform_basic)
print("Inferred classes:", balanced_dataset.classes)

# Split into train/val/test using random_split (70/15/15)
total = len(balanced_dataset)
train_n = int(0.7 * total)
val_n = int(0.15 * total)
test_n = total - train_n - val_n

# Perform the split
train_set, val_set, test_set = random_split(balanced_dataset, [train_n, val_n, test_n], generator=torch.Generator().manual_seed(RANDOM_SEED))
print(f"Split sizes -> Train: {len(train_set)} Val: {len(val_set)} Test: {len(test_set)}")

# Create DataLoaders directly from the split datasets
train_loader = DataLoader(train_set, batch_size=BATCH_SIZE, shuffle=True, num_workers=4)
val_loader = DataLoader(val_set, batch_size=BATCH_SIZE, shuffle=False, num_workers=4)
test_loader = DataLoader(test_set, batch_size=BATCH_SIZE, shuffle=False, num_workers=4)

print("Loaders ready.")

Loading dataset from DATA_ROOT: /content/drive/MyDrive/PR_Group_Project/unzipped
Inferred classes: ['H1', 'H2', 'H3', 'H5', 'H6']
Split sizes -> Train: 6363 Val: 1363 Test: 1364
Loaders ready.


/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(


In [8]:

# Models

import torch.nn.functional as F
# MODEL 1
class FungiCNN(nn.Module):
    def __init__(self, num_classes=5):
        super(FungiCNN, self).__init__()

        # Convolutional layers
        self.conv1 = nn.Conv2d(3, 32, kernel_size=3, padding=1)
        self.bn1 = nn.BatchNorm2d(32)

        self.conv2 = nn.Conv2d(32, 64, kernel_size=3, padding=1)
        self.bn2 = nn.BatchNorm2d(64)

        # Gentle downsampling with stride-2 conv
        self.pool1 = nn.Conv2d(64, 64, kernel_size=3, stride=2, padding=1)

        self.conv3 = nn.Conv2d(64, 128, kernel_size=3, padding=1)
        self.bn3 = nn.BatchNorm2d(128)

        self.conv4 = nn.Conv2d(128, 256, kernel_size=3, padding=1)
        self.bn4 = nn.BatchNorm2d(256)

        self.global_pool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(256, num_classes)

    def forward(self, x):
        x = F.relu(self.bn1(self.conv1(x)))
        x = F.relu(self.bn2(self.conv2(x)))
        x = F.relu(self.pool1(x))
        x = F.relu(self.bn3(self.conv3(x)))
        x = F.relu(self.bn4(self.conv4(x)))
        x = self.global_pool(x)
        x = x.view(x.size(0), -1)
        x = self.fc(x)
        x = F.softmax(x, dim=1)
        return x

base_model1 = FungiCNN(NUM_CLASSES)
if MODEL1_PTH is not None:
    try:
        base_model1.load_state_dict(torch.load(MODEL1_PTH, map_location=device))
        print("Loaded Model1 weights from", MODEL1_PTH)
    except Exception as ex:
        print("Could not load MODEL1_PTH:", ex)

#  MODEL 2: Normal CNN per specification
class NormalCNN(nn.Module):
    # K is the only parameter needed, representing NUM_CLASSES
    def __init__(self, num_classes = 5):
        super(NormalCNN, self).__init__()


        # Convolutional Layers
        # Input: 32x32x3
        self.conv1 = nn.Conv2d(3, 32, kernel_size=3, padding=3//2) # Output: 32x32x32
        self.pool1 = nn.MaxPool2d(2)                               # Output: 16x16x32

        self.conv2 = nn.Conv2d(32, 64, kernel_size=3, padding=3//2)  # Output: 16x16x64
        self.pool2 = nn.MaxPool2d(2)                               # Output: 8x8x64

        # Fixed Feature Calculation
        # Feature map size: (IMAGE_SIZE // 4) = 8
        # Final input features: x2 * 8 * 8 = 64 * 8 * 8 = 4096
        final_in_features = 64 * (IMAGE_SIZE // 4) * (IMAGE_SIZE // 4)

        # Fully Connected Layers
        self.fc1 = nn.Linear(final_in_features, 128)
        self.dropout = nn.Dropout(0.5)
        self.out = nn.Linear(128, num_classes)

    def forward(self, x):
        # 1. Conv -> ReLU -> Pool
        x = self.conv1(x)
        x = F.relu(x)
        x = self.pool1(x)

        # 2. Conv -> ReLU -> Pool
        x = self.conv2(x)
        x = F.relu(x)
        x = self.pool2(x)

        # 3. Flatten and apply FC layers
        x = torch.flatten(x, 1)

        x = self.fc1(x)
        x = F.relu(x)
        x = self.dropout(x)

        x = self.out(x)

        # 4. Softmax output
        x = F.softmax(x, dim=1)

        return x

base_model2 = NormalCNN(NUM_CLASSES)
print("Models instantiated.")

# Training and evaluation helpers
def train_one_epoch(model, loader, criterion, optimizer, device):
    model.train()
    running_loss = 0.0; correct = 0; total = 0
    # Use tqdm_notebook
    for imgs, labels in tqdm_notebook(loader, desc="Training Batch"):
        imgs = imgs.to(device); labels = labels.to(device)
        optimizer.zero_grad()
        outputs = model(imgs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        running_loss += loss.item() * imgs.size(0)
        preds = outputs.argmax(dim=1)
        correct += (preds == labels).sum().item()
        total += labels.size(0)
    return running_loss/total, correct/total

def evaluate(model, loader, criterion, device):
    model.eval()
    running_loss = 0.0
    all_preds = []; all_labels = []
    with torch.no_grad():
        # Use tqdm_notebook
        for imgs, labels in tqdm_notebook(loader, desc="Evaluation Batch"):
            imgs = imgs.to(device); labels = labels.to(device)
            outputs = model(imgs)
            loss = criterion(outputs, labels)
            running_loss += loss.item() * imgs.size(0)
            preds = outputs.argmax(dim=1)
            all_preds.append(preds.cpu().numpy()); all_labels.append(labels.cpu().numpy())
    all_preds = np.concatenate(all_preds); all_labels = np.concatenate(all_labels)
    acc = (all_preds == all_labels).sum() / len(all_labels)
    # Using 'macro' average for precision/recall
    prec = precision_score(all_labels, all_preds, average='macro', zero_division=0)
    rec = recall_score(all_labels, all_preds, average='macro', zero_division=0)
    conf = confusion_matrix(all_labels, all_preds)
    return running_loss/len(all_labels), acc, prec, rec, conf

Models instantiated.


In [10]:
# Main experiment: train Model1 and Model2 with 3 LRs x 3 optimizers -> 18 runs total
import json
from pathlib import Path

# Use tqdm_notebook in the outer loops for clarity
tqdm = tqdm_notebook

models_list = [('Model1', base_model1), ('Model2_NormalCNN', base_model2)]
opt_names = ['sgd', 'sgd_momentum', 'adam']

summary = []
best = {'acc': -1, 'run': None, 'path': None}

for model_name, model_template in tqdm(models_list, desc="Models"):
    for lr in tqdm(LR_LIST, desc=f"LRs for {model_name}"):
        for opt_name in tqdm(opt_names, desc=f"Optimizers for LR {lr}"):
            run_name = f"{model_name}_{opt_name}_lr{lr}"
            print(f"\n=== Starting Run: {run_name}")
            model = copy.deepcopy(model_template).to(device)
            criterion = nn.CrossEntropyLoss()

            # Optimizer setup
            if opt_name == 'sgd':
                optimizer = optim.SGD(model.parameters(), lr=lr)
            elif opt_name == 'sgd_momentum':
                optimizer = optim.SGD(model.parameters(), lr=lr, momentum=MOMENTUM)
            elif opt_name == 'adam':
                optimizer = optim.Adam(model.parameters(), lr=lr)
            scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=7, gamma=0.1)

            history = {'epoch':[], 'train_loss':[], 'train_acc':[], 'val_loss':[], 'val_acc':[]}
            best_val = -1.0; best_wts = copy.deepcopy(model.state_dict())

            for epoch in range(1, EPOCHS+1):
                t0 = time.time()
                # Pass a descriptive label to the helper's internal tqdm
                tr_loss, tr_acc = train_one_epoch(model, train_loader, criterion, optimizer, device)
                val_loss, val_acc, val_prec, val_rec, _ = evaluate(model, val_loader, criterion, device)
                scheduler.step()

                history['epoch'].append(epoch); history['train_loss'].append(tr_loss); history['train_acc'].append(tr_acc)
                history['val_loss'].append(val_loss); history['val_acc'].append(val_acc)
                print(f"Epoch {epoch}/{EPOCHS} | tr_acc={tr_acc:.4f} | val_acc={val_acc:.4f} | time={(time.time()-t0):.1f}s")

                if val_acc > best_val:
                    best_val = val_acc
                    best_wts = copy.deepcopy(model.state_dict())
                    print("--> New Best Validation Accuracy!")

            # Load best val weights and evaluate on test set
            model.load_state_dict(best_wts)
            print("\nEvaluating best model on Test Set...")
            test_loss, test_acc, test_prec, test_rec, conf = evaluate(model, test_loader, criterion, device)

            # Save model and logs
            model_path = Path(MODELS_DIR)/f"{run_name}.pth"
            torch.save(model.state_dict(), model_path)
            pd.DataFrame(history).to_csv(Path(LOGS_DIR)/f"{run_name}_history.csv", index=False)
            metrics = {'run': run_name, 'model': model_name, 'optimizer': opt_name, 'lr': lr,
                       'test_loss': test_loss, 'test_acc': test_acc, 'test_precision_macro': test_prec,
                       'test_recall_macro': test_rec, 'val_best_acc': best_val}
            pd.DataFrame([metrics]).to_csv(Path(LOGS_DIR)/f"{run_name}_metrics.csv", index=False)
            pd.DataFrame(conf).to_csv(Path(LOGS_DIR)/f"{run_name}_confusion.csv", index=False)
            print(f"Saved model and logs for {run_name}. Test Acc: {test_acc:.4f}")

            summary.append(metrics)
            if test_acc > best['acc']:
                best.update({'acc': test_acc, 'run': run_name, 'path': str(model_path)})



# Save summary of all runs
pd.DataFrame(summary).to_csv(Path(LOGS_DIR)/"all_runs_summary.csv", index=False)
print('\nDone with 18 runs. Best run overall:', best)

Models:   0%|          | 0/2 [00:00<?, ?it/s]

LRs for Model1:   0%|          | 0/3 [00:00<?, ?it/s]

Optimizers for LR 0.1:   0%|          | 0/3 [00:00<?, ?it/s]


=== Starting Run: Model1_sgd_lr0.1


Training Batch:   0%|          | 0/100 [00:00<?, ?it/s]

...

Evaluation Batch:   0%|          | 0/22 [00:00<?, ?it/s]

Epoch 20/20 | tr_acc=0.6695 | val_acc=0.6603 | time=36.0s

Evaluating best model on Test Set...


Evaluation Batch:   0%|          | 0/22 [00:00<?, ?it/s]

/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(


Saved model and logs for Model2_NormalCNN_adam_lr0.001. Test Acc: 0.6613

Done with 18 runs. Best run overall: {'acc': np.float64(0.7426686217008798), 'run': 'Model1_adam_lr0.001', 'path': '/content/drive/MyDrive/PR_Group_Project/results/models/Model1_adam_lr0.001.pth'}


In [11]:
# Compare the best model with pretrained ResNet50 and DenseNet121

print("Best found during experiments:", best)
if best['path'] is None:
    print("No best model found; ensure experiments ran. Aborting pretrained comparison.")
else:
    # For pretrained nets we need 224x224 inputs; create new dataloaders with resize to 224
    transform_pretrained = transforms.Compose([
        transforms.Resize((224,224)),
        transforms.ToTensor(),
        transforms.Normalize([0.485,0.456,0.406],[0.229,0.224,0.225])
    ])

    # Recreate datasets from the in-memory split sets with the new transform
    # Note: We can reuse the indices from the original split and apply the new transform to the base dataset.

    # Get the original full dataset (with original class names)
    original_dataset = datasets.ImageFolder(root=DATA_ROOT, transform=transform_pretrained)

    # Use the indices from the original random_split objects
    train_ds_pre = torch.utils.data.Subset(original_dataset, train_set.indices)
    val_ds_pre = torch.utils.data.Subset(original_dataset, val_set.indices)
    test_ds_pre = torch.utils.data.Subset(original_dataset, test_set.indices)

    train_loader_pre = DataLoader(train_ds_pre, batch_size=BATCH_SIZE, shuffle=True, num_workers=4)
    val_loader_pre = DataLoader(val_ds_pre, batch_size=BATCH_SIZE, shuffle=False, num_workers=4)
    test_loader_pre = DataLoader(test_ds_pre, batch_size=BATCH_SIZE, shuffle=False, num_workers=4)

    criterion = nn.CrossEntropyLoss()

    pretrained_models = ['resnet50','densenet121']
    pretrained_results = []

    for name in tqdm_notebook(pretrained_models, desc="Pretrained Models"):
        print(f"\n--- Starting Fine-Tuning for: {name}")
        if name=='resnet50':
            # Use weights=ResNet50_Weights.IMAGENET_V1 if on modern PyTorch, otherwise pretrained=True
            model = models.resnet50(weights='IMAGENET1K_V1')
            model.fc = nn.Linear(model.fc.in_features, NUM_CLASSES)
        elif name=='densenet121':
            # Use weights=DenseNet121_Weights.IMAGENET_V1 if on modern PyTorch, otherwise pretrained=True
            model = models.densenet121(weights='IMAGENET1K_V1')
            model.classifier = nn.Linear(model.classifier.in_features, NUM_CLASSES)
        model = model.to(device)

        # Only finetune the last layer if desired, but original code finetunes all.
        optimizer = optim.SGD(model.parameters(), lr=PRETRAINED_LR, momentum=MOMENTUM)

        # Simple fine-tuning loop (few epochs)
        for epoch in range(1, PRETRAINED_EPOCHS+1):
            print(f"[{name}] Epoch {epoch}/{PRETRAINED_EPOCHS}")
            tr_loss, tr_acc = train_one_epoch(model, train_loader_pre, criterion, optimizer, device)
            val_loss, val_acc, val_prec, val_rec, _ = evaluate(model, val_loader_pre, criterion, device)
            print(f"[{name}] Epoch {epoch}: train_acc={tr_acc:.4f} val_acc={val_acc:.4f}")

        # Evaluate on the test set
        print(f"\nEvaluating {name} on Test Set...")
        test_loss, test_acc, test_prec, test_rec, conf = evaluate(model, test_loader_pre, criterion, device)

        metrics = {'pretrained_model': name, 'test_loss': test_loss, 'test_acc': test_acc,
                   'test_precision_macro': test_prec, 'test_recall_macro': test_rec}

        pd.DataFrame([metrics]).to_csv(Path(LOGS_DIR)/f"pretrained_{name}_metrics.csv", index=False)
        pd.DataFrame(conf).to_csv(Path(LOGS_DIR)/f"pretrained_{name}_confusion.csv", index=False)
        pretrained_results.append(metrics)
        print(f"[{name}] Final Test Acc: {test_acc:.4f}")

    pd.DataFrame(pretrained_results).to_csv(Path(LOGS_DIR)/"pretrained_comparison.csv", index=False)
    print("Pretrained comparison saved to logs.")

Best found during experiments: {'acc': np.float64(0.7426686217008798), 'run': 'Model1_adam_lr0.001', 'path': '/content/drive/MyDrive/PR_Group_Project/results/models/Model1_adam_lr0.001.pth'}


/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(


Pretrained Models:   0%|          | 0/2 [00:00<?, ?it/s]


--- Starting Fine-Tuning for: resnet50
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth



  0%|          | 0.00/97.8M [00:00<?, ?B/s]
 16%|█▌        | 15.6M/97.8M [00:00<00:00, 163MB/s]
 36%|███▌      | 35.4M/97.8M [00:00<00:00, 189MB/s]
 60%|█████▉    | 58.5M/97.8M [00:00<00:00, 213MB/s]
100%|██████████| 97.8M/97.8M [00:00<00:00, 203MB/s]


...

Evaluation Batch:   0%|          | 0/22 [00:00<?, ?it/s]

[densenet121] Epoch 3: train_acc=0.8504 val_acc=0.8100

Evaluating densenet121 on Test Set...


Evaluation Batch:   0%|          | 0/22 [00:00<?, ?it/s]

/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(


[densenet121] Final Test Acc: 0.7859
Pretrained comparison saved to logs.
